In [59]:
# Import packages for building map
import numpy as np
import pandas as pd
import sodapy as sp
import pandas_bokeh as pbk
pbk.output_notebook()
from sodapy import Socrata
import matplotlib.pyplot as plt
import geopandas as gpd
#import descartes 
import json
from bokeh.io import show
from bokeh.models import (CDSView, ColorBar, ColumnDataSource, CustomJS,
                          CustomJSFilter, GeoJSONDataSource, HoverTool,
                          LinearColorMapper, Slider)
from bokeh.layouts import column, row, widgetbox
from bokeh.palettes import brewer
from bokeh.plotting import figure

Loading BokehJS ...

In [60]:
# Load file with state geometry
contiguous_cat = gpd.read_file('divisions-administratives-v1r0-comarques-1000000-20210122.shp')
# Load file with each region's population
df_pobl = pd.read_excel("PoblacioComarques.xls")
# importar el nostre dataset
client = Socrata("analisi.transparenciacatalunya.cat", None)
results = client.get("rmgc-ncpb", limit=17000)
# Convert to pandas DataFrame
results_df =  gpd.GeoDataFrame.from_records(results)
results_df.head()

any         zona                      dat    via      pk  \
0  2010  Zona urbana  2010-01-25T23:33:00.000     SE  999999   
1  2010    Carretera  2010-10-31T01:00:00.000  N-240     999   
2  2010    Carretera  2010-05-17T15:27:00.000   N-II    7087   
3  2010  Zona urbana  2010-08-21T22:30:00.000     SE  999999   
4  2010  Zona urbana  2010-05-07T17:45:00.000     SE  999999   

                 nommun           nomcom     nomdem f_morts f_ferits_greus  \
0     CANOVES I SAMALUS  Valles Oriental  Barcelona       0              1   
1                LLEIDA           Segria     Lleida       0              1   
2  FORNELLS DE LA SELVA          Girones     Girona       1              0   
3             BARCELONA       Barcelones  Barcelona       0              2   
4              BADALONA       Barcelones  Barcelona       0              1   

   ... d_superficie                                      d_tipus_via  \
0  ...    Sec i net  Via urbana( inclou carrer i carrer residencial)   
1  ...    Sec i net                           Carretera convencional   
2  ...    Sec i net                           Carretera convencional   
3  ...    Sec i net  Via urbana( inclou carrer i carrer residencial)   
4  ...    Sec i net  Via urbana( inclou carrer i carrer residencial)   

  d_titularitat_via d_tracat_altimetric                 d_vent    grupdialab  \
0                NA                  NA  Calma, vent molt suau       Feiners   
1           Estatal                 Pla  Calma, vent molt suau  CapDeSetmana   
2           Estatal     Rampa o pendent  Calma, vent molt suau       Feiners   
3                NA                  NA  Calma, vent molt suau  CapDeSetmana   
4                NA                  NA  Calma, vent molt suau  CapDeSetmana   

    hor gruphor                                   tipacc    tipdia  
0  2333     Nit           Col.lisió de vehicles en marxa  dill-dij  
1     1     Nit  Sortida de la calcada sense especificar        dg  
2  1527   Tarda           Col.lisió de vehicles en marxa  dill-dij  
3   223     Nit           Col.lisió de vehicles en marxa       dis  
4  1745   Tarda                     Bolcada a la calcada       div  

[5 rows x 58 columns]

In [61]:
# num d'accidents en funció de la comarca i ordenats alfabèticament respecte del nom de la comarca
com = pd.value_counts(results_df['nomcom'])
com = com.to_frame() # convertir a Data Frame
com = com.reset_index() # introduir un index (0, 1, 2...)
com = com.sort_values("index") # la columna de velocitat es diu index, ordenar-la
com = com.rename(columns={"index": "Comarca", "nomcom": "#accidents"}) # canviar els noms correctes
Comar = gpd.GeoDataFrame(com).set_index("Comarca")
Comar = Comar.reset_index()
Comar.head()

Comarca  #accidents
0        Alt Camp         146
1     Alt Emporda         563
2     Alt Penedes         397
3      Alt Urgell         187
4  Alta Ribagorca          30

In [62]:
geom = contiguous_cat[["NOMCOMAR", "geometry"]] # escollir les columnes: comarca i geometria de mcp
geom = geom.sort_values('NOMCOMAR') # ordenar alfabèticament
Geom = gpd.GeoDataFrame(geom).set_index("NOMCOMAR") # tornem a posar l'índex
Geom = Geom.reset_index()
Geom.head()

NOMCOMAR                                           geometry
0        Alt Camp  POLYGON ((373020.449 4590188.741, 372482.744 4...
1     Alt Empordà  MULTIPOLYGON (((513760.140 4662388.220, 513758...
2     Alt Penedès  POLYGON ((386593.300 4595896.200, 388616.100 4...
3      Alt Urgell  MULTIPOLYGON (((360800.100 4649174.000, 360624...
4  Alta Ribagorça  POLYGON ((327485.124 4721105.796, 327436.728 4...

In [63]:
# seleccionar columna de geometries
geometry = Geom[['geometry']]
# ordenem alfabèticament i deixem bonic el dataset de poblacions
df_pobl=df_pobl.sort_values('comarca')
df_pobl=pd.DataFrame(df_pobl).set_index('comarca')

In [64]:
df_pobl=df_pobl.reset_index()
df_pobl.head()

comarca    pobl  pobl_percent
0        Alt Camp   44168        0.0059
1     Alt Emporda  136981        0.0182
2     Alt Penedes  107724        0.0143
3      Alt Urgell   20201        0.0027
4  Alta Ribagorca    3813        0.0005

In [65]:
# seleccionar columnes pobl i pobl_percent
norm = df_pobl[['pobl', 'pobl_percent']]
combo = pd.concat([Comar, geometry, norm], axis=1) # juntem comarques, #accidents, geometria i poblacions
combo['accpercadamilhab'] = combo['#accidents']/combo['pobl']*1000 # afegim col per a #accidents per cada 1000 habitants
combo.head()

Comarca  #accidents  \
0        Alt Camp         146   
1     Alt Emporda         563   
2     Alt Penedes         397   
3      Alt Urgell         187   
4  Alta Ribagorca          30   

                                            geometry    pobl  pobl_percent  \
0  POLYGON ((373020.449 4590188.741, 372482.744 4...   44168        0.0059   
1  MULTIPOLYGON (((513760.140 4662388.220, 513758...  136981        0.0182   
2  POLYGON ((386593.300 4595896.200, 388616.100 4...  107724        0.0143   
3  MULTIPOLYGON (((360800.100 4649174.000, 360624...   20201        0.0027   
4  POLYGON ((327485.124 4721105.796, 327436.728 4...    3813        0.0005   

   accpercadamilhab  
0          3.305561  
1          4.110059  
2          3.685344  
3          9.256967  
4          7.867821

In [66]:
# Representacio interactiva
# Input GeoJSON source that contains features for plotting
geosource = GeoJSONDataSource(geojson = combo.to_json())

In [67]:
# Define color palettes
palette = brewer['BuGn'][8]
palette = palette[::-1] # reverse order of colors so higher values have darker colors

# Instantiate LinearColorMapper that linearly maps numbers in a range, into a sequence of colors.
color_mapper = LinearColorMapper(palette = palette, low = 0, high = 10)

# Define custom tick labels for color bar.
tick_labels = {'0': '0', '50': '500',
               '1000':'10000', '15000':'150000',
               '20000':'20000', '25000':'250000',
               '30000':'30000', '350000':'350000',
               '40000':'40000+'}

# Create color bar.
color_bar = ColorBar(color_mapper=color_mapper, label_standoff=8,width = 500, height = 20,
                     border_line_color=None,location = (0,0), orientation = 'horizontal',
                     major_label_overrides = tick_labels)

# Create figure object.
p = figure(title = "Nombre d'accidents per cada 1000 habitants 2010-18", plot_height = 600 ,
           plot_width = 600, toolbar_location = 'below',
           tools = "pan, wheel_zoom, box_zoom, reset")
p.xgrid.grid_line_color = None
p.ygrid.grid_line_color = None

# Add patch renderer to figure.
states = p.patches('xs','ys', source = geosource,
                   fill_color = {'field' :'accpercadamilhab', 'transform' : color_mapper},
                   line_color = 'gray', line_width = 0.25, fill_alpha = 1)

# Create hover tool
p.add_tools(HoverTool(renderers = [states],
                      tooltips = [('Comarca','@Comarca'),('# Accidents', '@accpercadamilhab')]))

# Specify layout
p.add_layout(color_bar, 'below')
p.xaxis.axis_label = 'New xlabel'
show(p)

In [68]:
alcohol = results_df[['nomdem','gruphor']]
alcohol.head()

nomdem gruphor
0  Barcelona     Nit
1     Lleida     Nit
2     Girona   Tarda
3  Barcelona     Nit
4  Barcelona   Tarda

In [69]:
alcohol = alcohol.groupby(['nomdem', 'gruphor']).size()
alcohol

nomdem     gruphor
Barcelona  Matí       4193
           Nit        1266
           Tarda      4875
Girona     Matí        982
           Nit         297
           Tarda      1127
Lleida     Matí        760
           Nit         181
           Tarda       851
Tarragona  Matí        979
           Nit         259
           Tarda      1004
dtype: int64

In [70]:
alcohol = alcohol.to_frame()
alcohol['pob']=[5463907,5463907,5463907,738976,738976,738976,429870,429870,429870,792001,792001,792001]
alcohol

0      pob
nomdem    gruphor               
Barcelona Matí     4193  5463907
          Nit      1266  5463907
          Tarda    4875  5463907
Girona    Matí      982   738976
          Nit       297   738976
          Tarda    1127   738976
Lleida    Matí      760   429870
          Nit       181   429870
          Tarda     851   429870
Tarragona Matí      979   792001
          Nit       259   792001
          Tarda    1004   792001

In [71]:
alcohol['norm']=(alcohol[0]/alcohol['pob'])*100000

In [72]:
alcohol.head()

0      pob        norm
nomdem    gruphor                           
Barcelona Matí     4193  5463907   76.739959
          Nit      1266  5463907   23.170233
          Tarda    4875  5463907   89.221870
Girona    Matí      982   738976  132.886589
          Nit       297   738976   40.190750

In [73]:
temps = results_df[['nomdem','d_superficie']]
temps.head()

nomdem d_superficie
0  Barcelona    Sec i net
1     Lleida    Sec i net
2     Girona    Sec i net
3  Barcelona    Sec i net
4  Barcelona    Sec i net

In [74]:
temps = temps.groupby(['nomdem', 'd_superficie']).size()
temps.head()

nomdem     d_superficie
Barcelona  Gelat             4
           Inundat          37
           Mullat          448
           Nevat             4
           Relliscós        67
dtype: int64

In [75]:
temps = temps.to_frame()
temps.head()

0
nomdem    d_superficie     
Barcelona Gelat           4
          Inundat        37
          Mullat        448
          Nevat           4
          Relliscós      67

In [76]:
temps = temps.reset_index()
temps.head()

nomdem d_superficie    0
0  Barcelona        Gelat    4
1  Barcelona      Inundat   37
2  Barcelona       Mullat  448
3  Barcelona        Nevat    4
4  Barcelona    Relliscós   67

In [77]:
temps_com = results_df[['nomcom','d_superficie']]
temps_com = temps_com.groupby(['nomcom', 'd_superficie']).size()
temps_com = temps_com.to_frame()
temps_com =temps_com.unstack()
temps_com = temps_com.fillna(0)
temps_com = temps_com.reset_index()
temps_com.columns = temps_com.columns.get_level_values(1)

In [78]:
temps_com.head()

d_superficie                  Gelat  Inundat  Mullat  Nevat  Relliscós  \
0                   Alt Camp    0.0      0.0     4.0    0.0        0.0   
1                Alt Emporda    0.0      2.0    20.0    0.0        6.0   
2                Alt Penedes    0.0      2.0    17.0    1.0        2.0   
3                 Alt Urgell    1.0      2.0    13.0    0.0        1.0   
4             Alta Ribagorca    0.0      1.0     3.0    0.0        0.0   

d_superficie  Sec i net  Sense especificar  
0                 142.0                0.0  
1                 534.0                1.0  
2                 374.0                1.0  
3                 170.0                0.0  
4                  26.0                0.0

temps_com

In [79]:
temps_com['percent_mal_estat'] = ((temps_com['Gelat']+temps_com['Inundat']+
                                   temps_com['Mullat']+temps_com['Nevat']+temps_com['Relliscós'])/(temps_com['Sec i net']+temps_com['Gelat']+temps_com['Inundat']+
                                   temps_com['Mullat']+temps_com['Nevat']+temps_com['Relliscós']))*100

In [80]:
temps_com.head()

d_superficie                  Gelat  Inundat  Mullat  Nevat  Relliscós  \
0                   Alt Camp    0.0      0.0     4.0    0.0        0.0   
1                Alt Emporda    0.0      2.0    20.0    0.0        6.0   
2                Alt Penedes    0.0      2.0    17.0    1.0        2.0   
3                 Alt Urgell    1.0      2.0    13.0    0.0        1.0   
4             Alta Ribagorca    0.0      1.0     3.0    0.0        0.0   

d_superficie  Sec i net  Sense especificar  percent_mal_estat  
0                 142.0                0.0           2.739726  
1                 534.0                1.0           4.982206  
2                 374.0                1.0           5.555556  
3                 170.0                0.0           9.090909  
4                  26.0                0.0          13.333333

In [81]:
combo['percent_mal_estat'] = temps_com['percent_mal_estat']

In [82]:
combo.head()

Comarca  #accidents  \
0        Alt Camp         146   
1     Alt Emporda         563   
2     Alt Penedes         397   
3      Alt Urgell         187   
4  Alta Ribagorca          30   

                                            geometry    pobl  pobl_percent  \
0  POLYGON ((373020.449 4590188.741, 372482.744 4...   44168        0.0059   
1  MULTIPOLYGON (((513760.140 4662388.220, 513758...  136981        0.0182   
2  POLYGON ((386593.300 4595896.200, 388616.100 4...  107724        0.0143   
3  MULTIPOLYGON (((360800.100 4649174.000, 360624...   20201        0.0027   
4  POLYGON ((327485.124 4721105.796, 327436.728 4...    3813        0.0005   

   accpercadamilhab  percent_mal_estat  
0          3.305561           2.739726  
1          4.110059           4.982206  
2          3.685344           5.555556  
3          9.256967           9.090909  
4          7.867821          13.333333

In [83]:
geosource = GeoJSONDataSource(geojson = combo.to_json())

# Define color palettes
palette = brewer['BuGn'][9]
palette = palette[::-1] # reverse order of colors so higher values have darker colors

# Instantiate LinearColorMapper that linearly maps numbers in a range, into a sequence of colors.
color_mapper = LinearColorMapper(palette = palette, low = 0, high = 18)

# Define custom tick labels for color bar.
tick_labels = {'0': '0', '50': '500',
               '1000':'10000', '15000':'150000',
               '20000':'20000', '25000':'250000',
               '30000':'30000', '350000':'350000',
               '40000':'40000+'}

# Create color bar.
color_bar = ColorBar(color_mapper=color_mapper, label_standoff=8,width = 500, height = 20,
                     border_line_color=None,location = (0,0), orientation = 'horizontal',
                     major_label_overrides = tick_labels)

# Create figure object.
p = figure(title = "percentatge d'accidents amb la carretera en mal estat", plot_height = 600 ,
           plot_width = 600, toolbar_location = 'below',
           tools = "pan, wheel_zoom, box_zoom, reset")
p.xgrid.grid_line_color = None
p.ygrid.grid_line_color = None

# Add patch renderer to figure.
states = p.patches('xs','ys', source = geosource,
                   fill_color = {'field' :'percent_mal_estat', 'transform' : color_mapper},
                   line_color = 'gray', line_width = 0.25, fill_alpha = 1)

# Create hover tool
p.add_tools(HoverTool(renderers = [states],
                      tooltips = [('Comarca','@Comarca'),('percent_mal_estat', '@percent_mal_estat')]))

# Specify layout
p.add_layout(color_bar, 'below')
p.xaxis.axis_label = 'New xlabel'
show(p)

In [84]:
combo =  gpd.GeoDataFrame.from_records(combo)
combo.crs = "epsg:25831"
p = combo.to_crs("epsg:4258").plot_bokeh(legend=False,title="Proportion of bad road conditions accidents", category='percent_mal_estat',show_figure=False)

show(p)

C:\Users\Daniel\anaconda3\lib\site-packages\pandas_bokeh\geoplot.py:144: ShapelyDeprecationWarning: Iteration over multi-part geometries is deprecated and will be removed in Shapely 2.0. Use the `geoms` property to access the constituent parts of a multi-part geometry.
  for polygon in geometry:


In [85]:
hora_com = results_df[['nomcom','gruphor']]
hora_com = hora_com.groupby(['nomcom', 'gruphor']).size()
hora_com = hora_com.to_frame()
hora_com = hora_com.unstack()
hora_com.columns = hora_com.columns.get_level_values(1)
hora_com['percent_nit'] = ((hora_com['Nit'])/(hora_com['Matí']+hora_com['Nit']+hora_com['Tarda']))*100
hora_com
hora_com = hora_com.reset_index(level = 0)
combo['percent_nit'] = hora_com['percent_nit']
combo

Comarca  #accidents  \
0            Alt Camp         146   
1         Alt Emporda         563   
2         Alt Penedes         397   
3          Alt Urgell         187   
4      Alta Ribagorca          30   
5               Anoia         283   
6               Bages         555   
7           Baix Camp         485   
8           Baix Ebre         297   
9        Baix Emporda         323   
10     Baix Llobregat        1356   
11       Baix Penedes         271   
12         Barcelones        3004   
13           Bergueda         187   
14           Cerdanya         117   
15   Conca de Barbera          69   
16             Garraf         346   
17          Garrigues          78   
18           Garrotxa         170   
19            Girones         507   
20            Maresme         786   
21            Moianès          90   
22            Montsia         219   
23            Noguera         229   
24              Osona         480   
25      Pallars Jussa          65   
26     Pallars Sobira          57   
27       Pla d'Urgell         123   
28    Pla de l'Estany         104   
29            Priorat          49   
30      Ribera d'Ebre         109   
31           Ripolles          60   
32            Segarra          89   
33             Segria         658   
34              Selva         595   
35           Solsones          95   
36         Tarragones         543   
37         Terra Alta          54   
38             Urgell          97   
39         Val d'Aran          53   
40  Valles Occidental        1899   
41    Valles Oriental         949   

                                             geometry     pobl  pobl_percent  \
0   POLYGON ((373020.449 4590188.741, 372482.744 4...    44168        0.0059   
1   MULTIPOLYGON (((513760.140 4662388.220, 513758...   136981        0.0182   
2   POLYGON ((386593.300 4595896.200, 388616.100 4...   107724        0.0143   
3   MULTIPOLYGON (((360800.100 4649174.000, 360624...    20201        0.0027   
4   POLYGON ((327485.124 4721105.796, 327436.728 4...     3813        0.0005   
5   POLYGON ((371426.378 4628557.172, 372106.708 4...   119129        0.0158   
6   POLYGON ((417259.067 4646530.811, 417513.903 4...   174703        0.0232   
7   MULTIPOLYGON (((334244.690 4546609.460, 334242...   190004        0.0252   
8   MULTIPOLYGON (((311847.200 4514855.880, 311833...    77170        0.0102   
9   MULTIPOLYGON (((498479.410 4622829.390, 498478...   131305        0.0174   
10  POLYGON ((402255.460 4605174.574, 402529.150 4...   812146        0.1077   
11  MULTIPOLYGON (((385851.064 4574022.148, 385800...   101979        0.0135   
12  MULTIPOLYGON (((432584.620 4580813.510, 432583...  2239915        0.2969   
13  MULTIPOLYGON (((391614.800 4661923.500, 391606...    38980        0.0052   
14  MULTIPOLYGON (((418200.724 4699919.287, 417775...    17695        0.0023   
15  POLYGON ((369548.800 4603947.800, 370045.800 4...    20013        0.0027   
16  MULTIPOLYGON (((386849.020 4561141.550, 386847...   146650        0.0194   
17  POLYGON ((327888.707 4605730.867, 328155.807 4...    18861        0.0025   
18  POLYGON ((462293.700 4686958.700, 462409.651 4...    55579        0.0074   
19  POLYGON ((494081.526 4662565.750, 494214.685 4...   186020        0.0247   
20  POLYGON ((477054.900 4621435.100, 478728.500 4...   442072        0.0586   
21  POLYGON ((428837.859 4639478.022, 428961.755 4...    13330        0.0018   
22  MULTIPOLYGON (((300644.450 4494148.850, 300643...    67875        0.0090   
23  POLYGON ((348524.976 4664596.302, 348224.932 4...    38206        0.0051   
24  MULTIPOLYGON (((418580.652 4643167.275, 418307...   156592        0.0208   
25  MULTIPOLYGON (((317718.105 4693389.714, 317738...    12932        0.0017   
26  POLYGON ((343204.997 4738566.787, 343217.247 4...     6897        0.0009   
27  MULTIPOLYGON (((341924.700 4618515.800, 341260...    36946        0.0049   
28  POLYGON ((482350.600 4671869.500, 483369.000 4...    31810        0.0042   
29  POLYGON ((320525.2

In [88]:
geosource = GeoJSONDataSource(geojson = combo.to_json())

# Define color palettes
palette = brewer['BuGn'][9]
palette = palette[::-1] # reverse order of colors so higher values have darker colors

# Instantiate LinearColorMapper that linearly maps numbers in a range, into a sequence of colors.
color_mapper = LinearColorMapper(palette = palette, low = 0, high = 18)

# Define custom tick labels for color bar.
tick_labels = {'0': '0', '50': '500',
               '1000':'10000', '15000':'150000',
               '20000':'20000', '25000':'250000',
               '30000':'30000', '350000':'350000',
               '40000':'40000+'}

# Create color bar.
color_bar = ColorBar(color_mapper=color_mapper, label_standoff=8,width = 500, height = 20,
                     border_line_color=None,location = (0,0), orientation = 'horizontal',
                     major_label_overrides = tick_labels)

# Create figure object.
p = figure(title = "percentatge d'accidents nocturns", plot_height = 600 ,
           plot_width = 600, toolbar_location = 'below',
           tools = "pan, wheel_zoom, box_zoom, reset")
p.xgrid.grid_line_color = None
p.ygrid.grid_line_color = None

# Add patch renderer to figure.
states = p.patches('xs','ys', source = geosource,
                   fill_color = {'field' :'percent_nit', 'transform' : color_mapper},
                   line_color = 'gray', line_width = 0.25, fill_alpha = 1)

# Create hover tool
p.add_tools(HoverTool(renderers = [states],
                      tooltips = [('Comarca','@Comarca'),('percent_nit', '@percent_nit')]))

# Specify layout
p.add_layout(color_bar, 'below')
p.xaxis.axis_label = 'New xlabel'
show(p)

In [89]:
combo =  gpd.GeoDataFrame.from_records(combo)
combo.crs = "epsg:25831"
p = combo.to_crs("epsg:4258").plot_bokeh(legend="Comarcas with car accident density", category='percent_nit',show_figure=False)

show(p)

C:\Users\Daniel\anaconda3\lib\site-packages\pandas_bokeh\geoplot.py:144: ShapelyDeprecationWarning: Iteration over multi-part geometries is deprecated and will be removed in Shapely 2.0. Use the `geoms` property to access the constituent parts of a multi-part geometry.
  for polygon in geometry:
